## Povezava do podatkovne baze

- modul pyodbc 
- povezovalni niz (eksplicitno, ali z uporabo DSN)

In [1]:
import pyodbc
from __future__ import print_function   # Kompatibilnost s Pythonom 2.7 in 3.x

# Eksplicitna prijava brez DSN
ConnectionStringEX = 'Driver={MySQL ODBC 8.0 Unicode Driver}; \
                    Server=pb.fri.uni-lj.si;Database=tup; \
                    User=tup;Password=tupvaje'
cnxnEX = pyodbc.connect(ConnectionStringEX)

# Privzete vrednosti DSN
ConnectionStringPG = 'DSN=Vaje-PG'
cnxnPG = pyodbc.connect(ConnectionStringPG)
# cnxnPG.cursor().execute("SET SCHEMA 'tup'")  # Lahko izvedemo v definiciji DSN pod "connect settings"

ConnectionStringMA = 'DSN=Vaje'
cnxnMA = pyodbc.connect(ConnectionStringMA)



## Kurzor 
- Osnovni element interakcije s PB. 
- Naredimo ga na osnovi konkretne povezave.
- Istočasno imamo lahko več kurzorjev.

In [10]:
cursor = cnxnMA.cursor()

In [11]:
print(cnxnMA.getinfo(pyodbc.SQL_DBMS_NAME),cnxnMA.getinfo(pyodbc.SQL_DBMS_VER))

MySQL 5.5.5-10.3.14-MariaDB-1:10.3.14+maria~trusty-log


In [14]:
cur1=cnxnMA.cursor()
rez1=cur1.execute('select * from jadralec')
print(rez1)

In [15]:
for v in rez1:
    print(v)
cur1.close()

(22, 'Darko', 7, 45.0)
(29, 'Borut', 1, 33.0)
(31, 'Lojze', 8, 55.5)
(32, 'Andrej', 8, 25.5)
(58, 'Rajko', 10, 35.0)
(64, 'Henrik', 7, 35.0)
(71, 'Zdravko', 10, 16.0)
(74, 'Henrik', 9, 35.0)
(85, 'Anze', 3, 25.5)
(95, 'Bine', 3, 63.5)


In [16]:
rez = cursor.execute("SELECT * FROM jadralec")

In [17]:
# Glava in vsebina (prvi poskus)
for g in rez.description:
    print(g[0],end="\t")
print()
for r in rez:
    for a in r:
        print(a,end="\t")
    print()

jid	ime	rating	starost	
22	Darko	7	45.0	
29	Borut	1	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	


In [18]:
rez = cursor.execute("SELECT * FROM jadralec")
telo = rez.fetchall()
#telo = rez.fetchone()
#telo = rez.fetchmany(2)

In [19]:
# Glava
for g in rez.description:
    print(g[0],end="\t")
print()


jid	ime	rating	starost	


In [20]:
# Vsebina in tipi
for r in telo:
    for a in r:
        print(a,type(a),end="\t")
    print()

22 <class 'int'>	Darko <class 'str'>	7 <class 'int'>	45.0 <class 'float'>	
29 <class 'int'>	Borut <class 'str'>	1 <class 'int'>	33.0 <class 'float'>	
31 <class 'int'>	Lojze <class 'str'>	8 <class 'int'>	55.5 <class 'float'>	
32 <class 'int'>	Andrej <class 'str'>	8 <class 'int'>	25.5 <class 'float'>	
58 <class 'int'>	Rajko <class 'str'>	10 <class 'int'>	35.0 <class 'float'>	
64 <class 'int'>	Henrik <class 'str'>	7 <class 'int'>	35.0 <class 'float'>	
71 <class 'int'>	Zdravko <class 'str'>	10 <class 'int'>	16.0 <class 'float'>	
74 <class 'int'>	Henrik <class 'str'>	9 <class 'int'>	35.0 <class 'float'>	
85 <class 'int'>	Anze <class 'str'>	3 <class 'int'>	25.5 <class 'float'>	
95 <class 'int'>	Bine <class 'str'>	3 <class 'int'>	63.5 <class 'float'>	


In [21]:
# Glava in vsebina (drugi poskus)
print("Vseh vrstic je", rez.rowcount)
for g in rez.description:
    print(g[0],end="\t")
print("\n"+"-"*31)
# Vsebina
for r in telo:
    for a in r:
        print(a,end="\t")
    print()

Vseh vrstic je 10
jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	1	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	


## Življenjska doba vsebine kurzorja

- le ena iteracija!

Metode kurzorja:
- fetchall(): vrne seznam vseh vrstic
- fetchone(): vrne naslednjo neprebrano vrstico (**pozor: to ni seznam!**)
- fetchmany(*n*): vrne naslednjih *n* neprebranih vrstic


## Naloga: poišči šifre najkrajših čolnov!

In [22]:
naj = cursor.execute("SELECT cid, dolzina FROM coln")

mind = 1000 # Nekaj velikega
mins = -1   # Nekaj neveljavnega 

for (s,d) in naj:
    if d < mind:
        (mins, mind) = (s,d)
        
print (mins, mind) 

101 34


### Bolje: kombinacija SQL in Pythona

In [23]:
naj = cursor.execute("""
        SELECT cid, dolzina 
        FROM coln 
        WHERE dolzina = (SELECT MIN(dolzina) FROM coln) 
      """)


for (s,d) in naj:       
   print (s, d) 

101 34
102 34


## Obravnava izjem


In [24]:
naj = cursor.execute("""
        SELECT cid, dolzina 
        FROM coln 
        WHERE dolzina = (SELECT MIN(dolzina) FROM coln) 
      """)

In [25]:
try:
    ConnectionStringBLA = 'Bla Bla'
    cnxnPG = pyodbc.connect(ConnectionStringBLA)
except Exception as e:
    print("NAPAKA v povezav!\n",e)

try:
    naj = cursor.execute(naj)
except pyodbc.DatabaseError as e:
    print("NAPAKA v poizvedbi!\n",e)
    


NAPAKA v povezav!
 ('IM002', '[IM002] [Microsoft][ODBC Driver Manager] Data source name not found and no default driver specified (0) (SQLDriverConnect); [IM002] [Microsoft][ODBC Driver Manager] Invalid connection string attribute (0)')


TypeError: The first argument to execute must be a string or unicode query.

## Zaključek dela: vedno zaprite povezave (po možnosti z obravnavo napak)!
Poženi dvakrat.


In [26]:
try:
    cnxnEX.close()
except Exception as e:
    print("Zapiranje povezave:",e)

try:
    cnxnPG.close()
except Exception as e:
    print("Zapiranje povezave:",e)

try:
    cnxnMA.close()
except Exception as e:
    print("Zapiranje povezave:",e)



